# Spoofed Speech Detection via Maximum Likelihood Estimation of Gaussian Mixture Models
The goal of synthetic speech detection is to determine whether a speech segment $S$ is natural or synthetic/converted speeach.

This notebook implements a Gaussian mixture model maximum likelihood (GMM-ML) classifier for synthetic (spoofed) speech detection. This approach uses regular mel frequency cepstral coefficients (MFCC) features and gives the best performance on the [ASVspoof 2015 dataset](https://www.idiap.ch/dataset/avspoof) among the standard classifiers (GMM-SV, GMM-UBM, ...). For more background information see: *Hanilçi, Cemal, Tomi Kinnunen, Md Sahidullah, and Aleksandr Sizov. "Classifiers for synthetic speech detection: a comparison." In INTERSPEECH 2015*. The scripts use the Python package [Bob.Bio.SPEAR 2.04](https://pypi.python.org/pypi/bob.bio.spear/2.0.4) for speaker recogntion.

This work is part of the ["DDoS Resilient Emergency Dispatch Center"](https://www.dhs.gov/science-and-technology/news/2015/09/04/dhs-st-awards-university-houston-26m-cyber-security-research) project at the University of Houston, funded by the Department of Homeland Security (DHS).


April 19, 2015

Lorenzo Rossi

(lorenzo **[dot]** rossi **[at]** gmail **[dot]** com)

In [1]:
import os
import time
import numpy as np
import pandas as pd
import scipy
import cqcc_ext
import cfcc_ext
import librosa
from cqcc import cqcc as CQCC
from bob.bio.spear import preprocessor, extractor
from bob.bio.gmm import algorithm
from bob.io.base import HDF5File
from bob.learn import em
from sklearn.metrics import classification_report, roc_curve, roc_auc_score

pd.set_option('display.max_rows', 300)

WAV_FOLDER = '/home/wujunting/data/ASVspoof2019/LA/' #'ASV2019dataset/wav/' # Path to folder containing speakers .wav subfolders
LABEL_FOLDER = '/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_cm_protocols/' #'ASV2019dataset/CM_protocol/' # Path to ground truth csv files

evalu_before = 'ASVspoof2019_LA_eval'
train_before = 'ASVspoof2019_LA_train'

EXT = '.wav'
%matplotlib inline

## Loading the Ground Truth
Load the dataframes (tables) with the labels for the training, development and evaluation (hold out) sets. Each subfolder corresponds to a different speaker. For example, T1 and D4 indicate the subfolders associated to the utterances and spoofed segments of speakers T1 and D4, respectively in training and development sets. Note that number of evaluation samples >> number of development samples >> testing samples.

You can either select the speakers in each set one by one, *e.g.*:
```
train_subfls = ['T1', 'T2']
``` 
will only load segments from speakers T1 and T2 for training,

or use all the available speakers in a certain subset by leaving the list empty, *e.g.*:
```
devel_subfls = [] 
```
will load all the available Dx speaker segments for the development stage. If you are running this notebook for the first time, you may want to start only with 2 or so speakers per set for sake of quick testing. All the scripts may take several hours to run on the full size datsets.

In [11]:
train_subfls = ['wav']#, 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'T13']  #T13 used instead of T10 for gender balance
devel_subfls = []#, 'D2', 'D3', 'D4', 'D5', 'D6', 'D7', 'D8', 'D9', 'D10']
evalu_subfls = ['wav']#, 'E2', 'E3', 'E4', 'E5', 'E6','E7',  'E8', 'E9', 'E10']
train = pd.read_csv(LABEL_FOLDER + 'ASVspoof2019.LA.cm.train.trn.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
train.sort_values(['folder', 'file'], inplace=True)
print(train)
devel = pd.read_csv(LABEL_FOLDER + 'ASVspoof2019.LA.cm.dev.trl.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
devel.sort_values(['folder', 'file'], inplace=True)
#print(devel)
evalu = pd.read_csv(LABEL_FOLDER +'ASVspoof2019.LA.cm.eval.30000.txt', sep=' ', header=None, names=['folder','file','default','method','source'])
print(evalu)
evalu.sort_values(['folder', 'file'], inplace=True)

label_2_class = {'bonafide':1, 'spoof':0}

print('training samples:',len(train))
print('development samples:',len(devel))
print('evaluation samples:',len(evalu))

        folder          file default method    source
2580   LA_0079  LA_T_1004644       -    A01     spoof
13980  LA_0079  LA_T_1006715       -    A04     spoof
10180  LA_0079  LA_T_1007408       -    A03     spoof
10181  LA_0079  LA_T_1017386       -    A03     spoof
6380   LA_0079  LA_T_1025525       -    A02     spoof
...        ...           ...     ...    ...       ...
13979  LA_0098  LA_T_9962675       -    A03     spoof
25379  LA_0098  LA_T_9982036       -    A06     spoof
21579  LA_0098  LA_T_9983869       -    A05     spoof
17779  LA_0098  LA_T_9984124       -    A04     spoof
2579   LA_0098  LA_T_9987202       -      -  bonafide

[25380 rows x 5 columns]
        folder          file default method source
0      LA_0039  LA_E_2834763       -    A11  spoof
1      LA_0014  LA_E_8877452       -    A14  spoof
2      LA_0040  LA_E_6828287       -    A16  spoof
3      LA_0022  LA_E_6977360       -    A09  spoof
4      LA_0031  LA_E_5932896       -    A13  spoof
...        ...      

## Speech Preprocessing and MFCC Extraction
Silence removal and MFCC feature extraction for training segments. More details about the bob.bio.spear involved libraries at:
https://www.idiap.ch/software/bob/docs/latest/bioidiap/bob.bio.spear/master/implemented.html

You can also skip this stage and load a set of feaures (see **Loading features** cell).

In [3]:
# Parameters
 # number of ceptral coefficients (implicit in extractor)
silence_removal_ratio = .1

In [13]:
subfolders = train_subfls
ground_truth = train

# initialize feature matrix
cqcc = []
cqcc_orig = []
cqcc_one = []
cqcc_two = []
cqcc_orig_one = []

y_list = []
#y = np.zeros((len(ground_truth),))
print("Extracting features for training stage.")

vad = preprocessor.Energy_Thr(ratio_threshold=silence_removal_ratio)
cepstrum = extractor.Cepstral()

k = 0
start_time = time.clock()

n_subfls = len(subfolders)
for folder in subfolders[0:n_subfls]:
    #print(folder, end=", ")
    train_folder = "".join([WAV_FOLDER,train_before,'/'])
    folder = "".join((train_folder,folder,'/'))
    print(folder)
    f_list = os.listdir(folder)
    # print(f_list)
    for f_name in f_list:
        if f_name.endswith(EXT):
        # ground truth
            try: 
                # 根据train中file(路径)字段，提取相应.wav文件的source(spoof or human)字段
                label = ground_truth[ground_truth.file==f_name[0:12]].source.values[0]
                #print(f_name[0:12], label)
            except IndexError:
                continue
            #y_list.append(label_2_class[label])
            # silence removal
            # print(vad)
            #rate,x = cqcc_ext.read(folder+f_name)
            #vad_data = cfcc_ext.vad(x)
            # CFCC extraction 
            #cqcc_feature = cqcc_ext.cqcc(vad_data,rate)
            #features.append(cqcc_feature)
            #k += 1
            
            
            
            y_list.append(label_2_class[label])
        # silence removal
        # print(f_name)
        # print(vad)
            x,fs = librosa.load(folder+f_name, sr = 16000)
            x = x.reshape(x.shape[0], 1)
            print(x)
            B = 96
            fmax = fs/2
            fmin = fmax/2**9
            d = 16
            cf = 19
            ZsdD = 'ZsdD'

            # MFCC extraction 
            CQcc, LogP_absCQT, TimeVec, FreqVec, Ures_LogP_absCQT, Ures_FreqVec, absCQT = CQCC(x, fs, B, fmax, fmin, d, cf, ZsdD)
            print("?")
            cqcc.append(CQcc)
            cqcc_orig.append(CQcc[:, :20])
            cqcc_one.append(CQcc[:, 20:40])
            cqcc_two.append(CQcc[:, 40:60])
            cqcc_orig_one.append(CQcc[:, :40])
            #print(features[:, :40].shape)
            #print("done")

# 这里是将人声与合成声进行了区分的，根据就是y
y = np.array(y_list)
Xf_cqcc = np.array(CQcc)
Xf_cqcc_orig = np.array(cqcc_orig)
Xf_cqcc_one = np.array(cqcc_one)
Xf_cqcc_two = np.array(cqcc_two)
Xf_cqcc_orig_one = np.array(cqcc_orig_one)
print(k,"files processed in",(time.clock()-start_time)/60,"minutes.")
np.save('Xf_cqcc.npy',Xf_cqcc)
np.save('Xf_cqcc_orig.npy',Xf_cqcc_orig)
np.save('Xf_cqcc_one.npy',Xf_cqcc_one)
np.save('Xf_cqcc_two.npy',Xf_cqcc_two)
np.save('Xf_cqcc_orig_one.npy',Xf_cqcc_orig_one)
np.save('y_cqcc.npy',y)
print('Feature and label matrices saved to disk')

Extracting features for training stage.
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_train/wav/
[[3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]
 ...
 [3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]]


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:19: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


?
[[-0.00268555]
 [-0.00259399]
 [-0.00259399]
 ...
 [-0.00064087]
 [-0.00094604]
 [-0.00091553]]
?
[[0.00274658]
 [0.00299072]
 [0.00259399]
 ...
 [0.00073242]
 [0.0010376 ]
 [0.00131226]]
?
[[3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]
 ...
 [3.0517578e-05]
 [6.1035156e-05]
 [0.0000000e+00]]
?
[[ 0.00027466]
 [ 0.00042725]
 [ 0.00033569]
 ...
 [-0.00018311]
 [-0.00024414]
 [-0.00045776]]
?
[[-0.00115967]
 [-0.00125122]
 [-0.0015564 ]
 ...
 [ 0.00375366]
 [ 0.00357056]
 [ 0.00302124]]
?
[[0.00140381]
 [0.0007019 ]
 [0.00027466]
 ...
 [0.00039673]
 [0.00039673]
 [0.00030518]]
?
[[ 3.0517578e-05]
 [ 3.0517578e-05]
 [ 3.0517578e-05]
 ...
 [-9.1552734e-05]
 [-9.1552734e-05]
 [-6.1035156e-05]]
?
[[ 0.00302124]
 [ 0.00305176]
 [ 0.00323486]
 ...
 [-0.00299072]
 [-0.00299072]
 [-0.00274658]]
?
[[-0.00430298]
 [-0.00405884]
 [-0.00405884]
 ...
 [ 0.00384521]
 [ 0.00402832]
 [ 0.00405884]]
?
[[ 9.1552734e-05]
 [ 9.1552734e-05]
 [ 9.1552734e-05]
 ...
 [-3.6621094e-04]
 [-1.8310547e-04]
 [-

?
[[-0.00115967]
 [-0.00131226]
 [-0.0010376 ]
 ...
 [-0.00259399]
 [-0.00286865]
 [-0.00305176]]
?
[[0.0027771 ]
 [0.00308228]
 [0.00305176]
 ...
 [0.00091553]
 [0.00097656]
 [0.0007019 ]]
?
[[ 3.0517578e-05]
 [ 3.0517578e-05]
 [ 3.0517578e-05]
 ...
 [ 3.0517578e-05]
 [-6.1035156e-05]
 [-6.1035156e-05]]
?
[[-0.00125122]
 [-0.00186157]
 [-0.00186157]
 ...
 [-0.00613403]
 [-0.00680542]
 [-0.00634766]]
?
[[-0.0027771 ]
 [-0.00308228]
 [-0.003479  ]
 ...
 [ 0.003479  ]
 [ 0.00332642]
 [ 0.00387573]]
?
[[3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]
 ...
 [0.0000000e+00]
 [0.0000000e+00]
 [0.0000000e+00]]
?
[[-8.2397461e-04]
 [-9.1552734e-04]
 [-8.2397461e-04]
 ...
 [ 0.0000000e+00]
 [ 9.1552734e-05]
 [ 1.2207031e-04]]
?
[[0.00097656]
 [0.00079346]
 [0.00067139]
 ...
 [0.0038147 ]
 [0.00442505]
 [0.00466919]]
?
[[ 0.00091553]
 [ 0.00085449]
 [ 0.00042725]
 ...
 [-0.00375366]
 [-0.00335693]
 [-0.00259399]]
?
[[3.0517578e-05]
 [3.0517578e-05]
 [0.0000000e+00]
 ...
 [0.0000000e+00]
 [0.000

?
[[0.00067139]
 [0.00057983]
 [0.00021362]
 ...
 [0.00061035]
 [0.00079346]
 [0.0005188 ]]
?
[[-0.00085449]
 [-0.00085449]
 [-0.00067139]
 ...
 [ 0.0005188 ]
 [ 0.00042725]
 [ 0.00030518]]
?
[[ 0.00308228]
 [ 0.00308228]
 [ 0.00296021]
 ...
 [-0.00222778]
 [-0.00204468]
 [-0.00192261]]
?
[[-1.8310547e-04]
 [ 2.4414062e-04]
 [ 6.1035156e-05]
 ...
 [ 6.1035156e-04]
 [ 1.4648438e-03]
 [ 9.4604492e-04]]
?
[[3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]
 ...
 [1.4648438e-03]
 [1.4038086e-03]
 [1.2512207e-03]]
?
[[ 0.00305176]
 [ 0.00296021]
 [ 0.00259399]
 ...
 [ 0.00588989]
 [-0.00015259]
 [ 0.00387573]]
?
[[ 0.00094604]
 [ 0.00112915]
 [ 0.0010376 ]
 ...
 [-0.00015259]
 [-0.00012207]
 [-0.00012207]]
?
[[3.0517578e-05]
 [3.0517578e-05]
 [3.0517578e-05]
 ...
 [0.0000000e+00]
 [0.0000000e+00]
 [0.0000000e+00]]
?
[[-0.0007019 ]
 [-0.00076294]
 [-0.00073242]
 ...
 [-0.00030518]
 [-0.00045776]
 [-0.00054932]]
?
[[9.1552734e-05]
 [9.1552734e-05]
 [9.1552734e-05]
 ...
 [3.0517578e-05]
 [6.103

...

?
[[ 0.0000000e+00]
 [ 0.0000000e+00]
 [ 0.0000000e+00]
 ...
 [-3.0517578e-05]
 [-3.0517578e-05]
 [-3.0517578e-05]]
?
[[-3.0517578e-05]
 [-3.0517578e-05]
 [-3.0517578e-05]
 ...
 [ 6.1035156e-05]
 [-9.1552734e-05]
 [-9.1552734e-05]]
?
[[ 0.00128174]
 [ 0.0012207 ]
 [-0.00018311]
 ...
 [ 0.00064087]
 [ 0.00033569]
 [ 0.00064087]]
?
[[-0.00030518]
 [-0.00030518]
 [-0.00030518]
 ...
 [-0.00149536]
 [-0.00338745]
 [-0.00384521]]
?
[[ 0.0000000e+00]
 [-3.0517578e-05]
 [-2.4414062e-04]
 ...
 [-1.0375977e-03]
 [-8.8500977e-04]
 [-7.6293945e-04]]
?
[[0.00057983]
 [0.00073242]
 [0.00076294]
 ...
 [0.00119019]
 [0.00131226]
 [0.00134277]]
?
[[0.00411987]
 [0.00430298]
 [0.00473022]
 ...
 [0.00485229]
 [0.00552368]
 [0.00588989]]
?
[[ 0.01367188]
 [ 0.00997925]
 [ 0.01055908]
 ...
 [-0.01263428]
 [-0.0088501 ]
 [-0.00643921]]
?
[[ 0.00231934]
 [ 0.00210571]
 [ 0.00170898]
 ...
 [-0.00964355]
 [-0.00973511]
 [-0.00979614]]
?
[[ 0.00085449]
 [ 0.00097656]
 [ 0.00073242]
 ...
 [-0.00106812]
 [-0.0010

?
[[0.00302124]
 [0.00228882]
 [0.00146484]
 ...
 [0.00045776]
 [0.00033569]
 [0.00036621]]
?
[[-0.00100708]
 [-0.00100708]
 [-0.00079346]
 ...
 [ 0.        ]
 [-0.00012207]
 [-0.00015259]]
?
[[ 1.5258789e-04]
 [ 2.4414062e-04]
 [ 9.1552734e-05]
 ...
 [-2.1362305e-04]
 [ 6.1035156e-05]
 [ 1.2207031e-04]]
?
[[6.1035156e-05]
 [6.1035156e-05]
 [6.1035156e-05]
 ...
 [6.1035156e-05]
 [6.1035156e-05]
 [6.1035156e-05]]
?
[[ 0.0038147 ]
 [ 0.00323486]
 [ 0.00289917]
 ...
 [-0.00097656]
 [-0.00170898]
 [-0.00180054]]
?
[[-0.00280762]
 [-0.00305176]
 [-0.00338745]
 ...
 [-0.00234985]
 [-0.00234985]
 [-0.00250244]]
?
[[0.00143433]
 [0.00125122]
 [0.00109863]
 ...
 [0.00024414]
 [0.00027466]
 [0.00027466]]
?
[[0.00332642]
 [0.00308228]
 [0.00283813]
 ...
 [0.00390625]
 [0.00183105]
 [0.00241089]]
?
[[-3.0517578e-05]
 [-6.1035156e-05]
 [ 3.0517578e-04]
 ...
 [-3.5095215e-03]
 [-3.2653809e-03]
 [-2.9296875e-03]]
?
[[-0.0065918 ]
 [-0.00726318]
 [-0.00598145]
 ...
 [ 0.00393677]
 [ 0.00518799]
 [ 0.0

?
[[-0.00064087]
 [-0.00036621]
 [-0.00027466]
 ...
 [-0.00088501]
 [-0.00064087]
 [-0.00012207]]
?
[[ 6.1035156e-05]
 [ 6.1035156e-05]
 [ 6.1035156e-05]
 ...
 [ 0.0000000e+00]
 [-9.1552734e-05]
 [-2.4414062e-04]]
?
[[ 6.1035156e-05]
 [ 6.1035156e-05]
 [ 6.1035156e-05]
 ...
 [-3.9672852e-04]
 [-1.0375977e-03]
 [-1.0375977e-03]]
?
[[ 6.1035156e-05]
 [ 6.1035156e-05]
 [ 6.1035156e-05]
 ...
 [-3.0517578e-05]
 [-3.0517578e-05]
 [ 0.0000000e+00]]
?
[[-0.00540161]
 [-0.00531006]
 [-0.00512695]
 ...
 [-0.00027466]
 [-0.00067139]
 [-0.00076294]]
?
[[ 0.00506592]
 [ 0.00524902]
 [ 0.0055542 ]
 ...
 [ 0.00097656]
 [ 0.00091553]
 [-0.00305176]]
?
[[ 0.00012207]
 [-0.00018311]
 [-0.00027466]
 ...
 [-0.00030518]
 [-0.00012207]
 [ 0.00015259]]
?
[[-0.00024414]
 [-0.00061035]
 [-0.00064087]
 ...
 [ 0.00253296]
 [ 0.00180054]
 [ 0.0015564 ]]
?
[[ 0.00192261]
 [ 0.00167847]
 [ 0.00143433]
 ...
 [-0.00265503]
 [-0.00265503]
 [-0.00280762]]
?
[[-3.0517578e-04]
 [-3.0517578e-04]
 [-2.4414062e-04]
 ...
 [ 

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:82: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


Feature and label matrices saved to disk


In [16]:
print(Xf_mfcc[y==0].shape)

(22800,)


In [69]:
np.vstack(Xf[y==1]).shape

(34771, 84)

In [80]:
ground_truth

folder      file default    method    source  z  z_gmm  score_gmm
107206     E2  E200001s       -     spoof     spoof  0    1.0   7.622108
98412      E2  E200002s       -     spoof     spoof  0    1.0  10.544859
102443     E2  E200003h       -  bonafide  bonafide  1    0.0  -2.888099
103712     E2  E200004s       -     spoof     spoof  0    0.0  -2.797664
98984      E2  E200005h       -  bonafide  bonafide  1    1.0  17.829845
...       ...       ...     ...       ...       ... ..    ...        ...
105581     E2  E208996h       -  bonafide  bonafide  1    0.0  -3.521843
100661     E2  E208997h       -  bonafide  bonafide  1    0.0  -3.759985
106825     E2  E208998s       -     spoof     spoof  0    1.0   6.707735
102766     E2  E208999h       -  bonafide  bonafide  1    1.0   7.150391
105172     E2  E209000h       -  bonafide  bonafide  1    0.0  -2.000744

[9000 rows x 8 columns]

### Saving features

In [18]:
np.save('Xf_mfcc.npy',Xf_mfcc)
np.save('Xf_mfcc_orig.npy',Xf_mfcc_orig)
np.save('Xf_mfcc_one.npy',Xf_mfcc_one)
np.save('Xf_mfcc_two.npy',Xf_mfcc_two)
np.save('Xf_mfcc_orig_one.npy',Xf_mfcc_orig_one)
np.save('y_mfcc.npy',y)
print('Feature and label matrices saved to disk')

Feature and label matrices saved to disk


### Loading features

In [2]:
# Load already extracter features to skip the preprocessing-extraction stage
# Xf = np.load('train_features_10.npy')
# y = np.load('y_10.npy')
Xf = np.load('Xf_cqcc_two.npy',allow_pickle=True)
y = np.load('y_cqcc.npy',allow_pickle=True)

In [5]:
print(Xf.shape)
print(Xf[y==1].shape)

(25380,)
(2580,)


# GMM - ML Classification

## GMM Training
Train the GMMs for natural and synthetic speach. For documentation on bob.bio k-means and GMM machines see:
https://pythonhosted.org/bob.learn.em/guide.html

You can also skip the training stage and load an already trained GMM model (see cell **Loading GMM Model**).

In [3]:
# Parameters of the GMM machines
n_gaussians = 256 # number of Gaussians
max_iterats = 25 # maximum number of iterations
n_ceps = 20

### GMM for natural speech 

In [4]:
# Initialize and train k-means machine: the means will initialize EM algorithm for GMM machine
start_time = time.clock()
kmeans_nat = em.KMeansMachine(n_gaussians,n_ceps)
kmeansTrainer = em.KMeansTrainer()
print(kmeans_nat.shape,Xf[y==1].shape)
em.train(kmeansTrainer, kmeans_nat, np.vstack(Xf[y==1]), max_iterations = max_iterats, convergence_threshold = 1e-5)
#kmeans_nat.means

# initialize and train GMM machine
gmm_nat = em.GMMMachine(n_gaussians,n_ceps)
trainer = em.ML_GMMTrainer(True, True, True)
gmm_nat.means = kmeans_nat.means
em.train(trainer, gmm_nat, np.vstack(Xf[y==1]), max_iterations = max_iterats, convergence_threshold = 1e-5)
gmm_nat.save(HDF5File('pzb_cqcc_two_nat.hdf5', 'w'))
print("Done in:", (time.clock() - start_time)/60, "minutes")
print(gmm_nat)

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


(256, 20) (2580,)
Done in: 23.10620845 minutes


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:15: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  from ipykernel import kernelapp as app


### GMM for synthetic speech

In [5]:
# initialize and train k-means machine: the means will initialize EM algorithm for GMM machine
start_time = time.clock()
kmeans_synt = em.KMeansMachine(n_gaussians,n_ceps)
kmeansTrainer = em.KMeansTrainer()
print(kmeans_synt.shape,Xf[y==0].shape)
em.train(kmeansTrainer, kmeans_synt, np.vstack(Xf[y==0]), max_iterations = max_iterats, convergence_threshold = 1e-5)

# initialize and train GMM machine
gmm_synt = em.GMMMachine(n_gaussians,n_ceps)
trainer = em.ML_GMMTrainer(True, True, True)
gmm_synt.means = kmeans_synt.means
em.train(trainer, gmm_synt, np.vstack(Xf[y==0]), max_iterations = max_iterats, convergence_threshold = 1e-5)
print("Done in:", (time.clock() - start_time)/60, "minutes")
gmm_synt.save(HDF5File('pzb_cqcc_one_synt.hdf5', 'w'))
print(gmm_synt)

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


(256, 20) (22800,)
Done in: 197.55267311666665 minutes


/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:13: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  del sys.path[0]


### Saving GMM model

In [52]:
gmm_nat.save(HDF5File('gmm_nat_500seg.hdf5', 'w'))
gmm_synt.save(HDF5File('gmm_synt_500seg.hdf5', 'w'))

### Loading GMM model

In [55]:
gmm_nat = em.GMMMachine()
gmm_nat.load(HDF5File('gmm_nat_500seg.hdf5', 'r'))
gmm_synt = em.GMMMachine()
gmm_synt.load(HDF5File('gmm_synt_500seg.hdf5','r'))

In [ ]:
np.save('p_gmm_ml_eval_10.npy',llr_score)
np.save('z_gmm_ml_eval_est_10.npy',z_gmm)

## GMM-ML Scoring
Extract the features for the testing data, compute the likelihood ratio test and  compute ROC AUC and estimated EER scores.

In [14]:
status = 'evalu' # 'devel'(= test) OR 'evalu'(= hold out)
start_time = time.clock()
F_FILE = np.array([])

if status == 'devel':
    subfolders = devel_subfls
    ground_truth = devel
elif status == 'evalu':
    subfolders = evalu_subfls
    ground_truth = evalu
n_subfls = len(subfolders)
# initialize score and class arrays
gmm_nat_score = np.zeros(len(ground_truth),)
gmm_synt_score = np.zeros(len(ground_truth),)
llr_gmm_score = np.zeros(len(ground_truth),)
z_gmm = np.zeros(len(ground_truth),)
print(status)

vad = preprocessor.Energy_Thr(ratio_threshold=.1)
cepstrum = extractor.Cepstral()

k = 0
thr = .5

#speaker = ground_truth[ground_truth.folder==speaker_id]
f_list = list(ground_truth.file)
evalu_folder = "".join([WAV_FOLDER,evalu_before,'/'])
folder = "".join([evalu_folder,evalu_subfls[0],'/'])
#print(f_list)
#print(folder)
for f in f_list:
    if isinstance(f,str):
        f_name = "".join([folder,f,EXT])
    if os.path.exists(f_name):
        # silence removal
        # print(f_name)
        # print(vad)
        x,fs = librosa.load(f_name, sr = 16000)
        x = x.reshape(x.shape[0], 1)
        print(f_name)
        B = 96
        fmax = fs/2
        fmin = fmax/2**9
        d = 16
        cf = 19
        ZsdD = 'ZsdD'
        CQcc, LogP_absCQT, TimeVec, FreqVec, Ures_LogP_absCQT, Ures_FreqVec, absCQT = CQCC(x, fs, B, fmax, fmin, d, cf, ZsdD)
        # Log likelihood ratio computation
        gmm_nat_score[k] = gmm_nat(CQcc[: , 40:60])
        gmm_synt_score[k] = gmm_synt(CQcc[: , 40:60])
        llr_gmm_score[k] = gmm_nat_score[k] - gmm_synt_score[k]
        z_gmm[k] = int(llr_gmm_score[k]>0)
        
        #class_2_label={0:'spoof',1:'bonafide'}
        #if label_2_class[ground_truth.iloc[k].source] != z_gmm[k]:
        #    F_FILE = np.append(F_FILE,ground_truth.iloc[k].file)
            
    k += 1
    

ground_truth['z'] = ground_truth.source.map(lambda x: int(x=='bonafide'))
ground_truth['z_gmm'] = z_gmm
ground_truth['score_gmm'] = llr_gmm_score
ground_truth['gmm_nat_score'] = gmm_nat_score
ground_truth['gmm_synt_score'] = gmm_synt_score
#print(roc_auc_score(ground_truth.z, ground_truth.z_gmm))
print(k,"files processed in",(time.clock()-start_time)/60,"minutes.")

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:2: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  


evalu
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1000273.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1046146.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1108783.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1162514.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1168493.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1209085.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1223182.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1238082.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1252063.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1259345.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1305592.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1305675.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3261040.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3280186.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3289636.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3294660.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3299128.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3326418.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3334486.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3388962.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3395592.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3451203.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3485223.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3493938.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5208384.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5212579.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5241093.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5288159.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5299530.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5302991.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5309654.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5325482.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5375953.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5423185.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5434482.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5451386.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7403387.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7456525.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7465503.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7468621.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7470423.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7491520.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7509372.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7534998.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7565818.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7598674.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7615821.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7632824.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

...

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3582930.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3737819.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3957992.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4220286.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4228891.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4366255.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4439959.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4660937.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4701828.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4729427.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4772853.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5033229.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3885033.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_3902702.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4180632.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4213874.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4523976.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_4691178.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5188210.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5263265.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5384940.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5403736.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_5438066.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_6162524.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7884603.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_7986426.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_8610376.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_8636129.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9094036.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9174730.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9211880.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9226172.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9270540.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9296664.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9318500.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9779446.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9696236.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_9905727.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1007872.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1109756.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1194237.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1235824.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1280848.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1370474.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1486783.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1537728.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_1955851.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA_eval/wav/LA_E_2044500.wav
/home/wujunting/data/ASVspoof2019/LA/ASVspoof2019_LA

/home/wujunting/anaconda3/envs/bob_py3/lib/python3.7/site-packages/ipykernel_launcher.py:67: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


In [11]:
F_FILE

array(['EHUM10001', 'EHUM10003', 'EHUM10004', 'EHUM10005', 'EHUM10006',
       'EHUM10008', 'EHUM10009', 'EHUM10010', 'EHUM10012', 'EHUM10013',
       'EHUM10016', 'EHUM10017', 'EHUM10022', 'EHUM10023', 'EHUM10024',
       'EHUM10025', 'EHUM10026', 'EHUM10027', 'EHUM10028', 'EHUM10029',
       'EHUM10030', 'EHUM10031', 'EHUM10032', 'EHUM10033', 'EHUM10034',
       'EHUM10035', 'EHUM10036', 'EHUM10037', 'EHUM10038', 'EHUM10039',
       'EHUM10040', 'EHUM10041', 'EHUM10042', 'EHUM10043', 'EHUM10044',
       'EHUM10045', 'EHUM10046', 'EHUM10047', 'EHUM10048', 'EHUM10049',
       'EHUM10050', 'EHUM10051', 'EHUM10052', 'EHUM10053', 'EHUM10054',
       'EHUM10055', 'EHUM10057', 'EHUM10058', 'EHUM10059', 'EHUM10060',
       'EHUM10061', 'EHUM10062', 'EHUM10063', 'EHUM10064', 'EHUM10065',
       'EHUM10066', 'EHUM10067', 'EHUM10069', 'EHUM10070', 'EHUM10071',
       'EHUM10072', 'EHUM10073', 'EHUM10074', 'EHUM10075', 'EHUM10078',
       'EHUM10080', 'EHUM10082', 'EHUM10083', 'EHUM10084', 'EHUM

In [13]:
# Performance evaluation

#实际humans个数
humans = sum(ground_truth.z==1)
print("实际humans个数:", humans)

#实际spoofed个数
spoofed = sum(ground_truth.z==0)
print("实际spoofed个数:", spoofed)

#预测humans个数
pre_humans = sum(ground_truth.z_gmm==1)
print("预测humans个数:", pre_humans)

#预测spoofed个数
pre_spoofed = sum(ground_truth.z_gmm==0)
print("预测spoofed个数:", pre_spoofed)

tp = 0
tn = 0
fp = 0
fn = 0
for i in ground_truth.index:
    if ground_truth.z[i] == 1 and ground_truth.z_gmm[i]==1:
        tp = tp + 1
    elif ground_truth.z[i] == 1 and ground_truth.z_gmm[i]==0:
        fn = fn + 1
    elif ground_truth.z[i] == 0 and ground_truth.z_gmm[i]==0:
        tn = tn + 1
    elif ground_truth.z[i] == 0 and ground_truth.z_gmm[i]==1:
        fp = fp + 1
print("TP_Num:", tp)
print("TN_Num:", tn)
print("FP_Num:", fp)
print("FN_Num:", fn)

tpr = tp/(tp+fn)
fpr = fp/(fp+tn)
tnr = tn/(fp+tn)
fnr = fn/(tp+fn)
acc = (tp+tn)/(tp+fp+tn+fn)
eer = (fpr*fnr)/(fpr+fnr)
print("TPR:", tpr)
print("FPR:", fpr)
print("TNR:", tnr)
print("FNR:", fnr)
print("ROC:", roc_auc_score(ground_truth.z, ground_truth.z_gmm))
print("Accuracy:", acc)
print("EER:", eer)

# humans = z_gmm[z_dvl==0]
# spoofed = z_gmm[z_dvl==1]
# fnr = 100*(1-(humans<thr).sum()/len(humans))
# fpr = 100*(1-(spoofed>=thr).sum()/len(spoofed))
# print("ROC AUC score:", roc_auc_score(z_dvl,z_gmm))
# print("False negative rate %:", fnr)
# print("False positive rate %:", fpr)
# print("EER %: <=", (fnr+fpr)/2)

实际humans个数: 3116
实际spoofed个数: 26884
预测humans个数: 16522
预测spoofed个数: 13478
TP_Num: 2121
TN_Num: 12483
FP_Num: 14401
FN_Num: 995
TPR: 0.6806803594351734
FPR: 0.5356717750334772
TNR: 0.4643282249665228
FNR: 0.3193196405648267
ROC: 0.5725042922008481
Accuracy: 0.4868
EER: 0.20006109481779455


In [62]:
method = {}
for index, row in ground_truth.iterrows():
    if row['z'] != row['z_gmm']:
        if row['method'] in method:
            method[row['method']] = method[row['method']] + 1
        else:
            method[row['method']] = 1
print(method)

{'-': 6757, 'A07': 17, 'A16': 18, 'A10': 28, 'A12': 21, 'A11': 25, 'A13': 6, 'A15': 4, 'A18': 13, 'A17': 14, 'A19': 39, 'A08': 2}


In [47]:
ground_truth

folder        file method source  z  z_gmm  score_gmm
2597     D1  D1_1002598  human  human  1    1.0   1.447147
2598     D1  D1_1002599  human  human  1    1.0   2.336380
2599     D1  D1_1002600  human  human  1    1.0   3.082637
2600     D1  D1_1002601  human  human  1    1.0   3.716948
2601     D1  D1_1002602  human  human  1    1.0   0.914256
...     ...         ...    ...    ... ..    ...        ...
7767     D3  D3_1007768     S1  spoof  0    0.0  -2.641017
7768     D3  D3_1007769     S2  spoof  0    0.0  -0.571958
7769     D3  D3_1007770     S3  spoof  0    0.0  -5.441518
7770     D3  D3_1007771     S4  spoof  0    0.0  -4.762759
7771     D3  D3_1007772     S5  spoof  0    0.0  -1.451432

[3050 rows x 7 columns]

### EER computation

Adjust the threshold $thr$ to reduce $FNR-FPR$ for a more accurate estimate of the $EER$.

The Equal Error Rate ($EER$) is the value where the false negative rate ($FNR$) equals the false positive rate ($FPR$). It's an error metric commonly used to characterize biometric systems.

In [47]:
thr = -.115
pz = llr_gmm_score
spoofed = pz[np.array(ground_truth.z)==1]
humans = pz[np.array(ground_truth.z)==0]
fnr = 100*(humans>thr).sum()/len(humans)
fpr = 100*(spoofed<=thr).sum()/len(spoofed)
print("False negative vs positive rates %:", fnr, fpr)
print("FNR - FPR %:", fnr-fpr)
if np.abs(fnr-fpr) <.25:
    print("EER =", (fnr+fpr)/2,"%")
else:
    print("EER ~", (fnr+fpr)/2,"%")

False negative vs positive rates %: 0.3345997002544352 99.53318745441284
FNR - FPR %: -99.19858775415841
EER ~ 49.933893577333635 %
